In [14]:
import pandas as pd
import warnings

warnings.filterwarnings("ignore")


exclusions = pd.read_csv('annotations_excluded.csv')

metadata = (
    pd.read_csv('metadata.csv', usecols=
                [
                    'scan_id',
                    'x-offset',
                    'y-offset',
                    'z-offset',
                    'x-spacing',
                    'y-spacing',
                    'z-spacing',
                    'x-pixels',
                    'y-pixels',
                    'slices'    
                ]
            )
)

metadata['scan_id'] = metadata.scan_id.str.replace('.mhd','')

exclusions.seriesuid.values[0]
metadata.scan_id.values[0]

'1.3.6.1.4.1.14519.5.2.1.6279.6001.885292267869246639232975687131'

In [31]:
from collections import namedtuple
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import pandas as pd
from pathlib import Path
import subprocess
import SimpleITK as sitk
from typing import List


combined = pd.merge(exclusions, metadata, left_on='seriesuid', right_on='scan_id', how='outer')  

DisplayTuple = namedtuple('DisplayTuple',['nodule_type','scan_id', 'image', 'xyz_coords', 'irc_coords', 'diameter'])

IrcTuple = namedtuple('IrcTuple',['index','row','col'])

XyzTuple = namedtuple('XyzTuple',['x','y','z'])

class SummitScan:
    """
    Author: John McCabe
    Description:  

    Attributes:
        pixel_array
        voxel_size
        origin
        orientation
    """
    def __init__(self, scan_uid, metadata, image) -> None:
        super().__init__()
        self.scan_uid = scan_uid
        self.metadata = metadata
        self.image = image

        # Pull out the salient bits of info needed
        self.origin = self.metadata.GetOrigin()
        self.voxel_size = self.metadata.GetSpacing()
        self.orientation = np.array(self.metadata.GetDirection()).reshape(3,3)

    @classmethod
    def load_scan(cls, path, type='MetaImageIO'):
        """
        Loads the scan from raw. Keeps all properties as part of the slices. 
        """

        # unique identifier can be found from file name
        scan_uid = Path(path).name.split('.')[0]

        # read in the scan
        if type == 'MetaImageIO':
            metadata = sitk.ReadImage(path)
            image = np.array(sitk.GetArrayFromImage(metadata), dtype=np.float32)

        return cls(scan_uid, metadata, image)

def xyz2irc(coord_xyz, origin, voxel_size, orientation=np.array([[1,0,0],[0,1,0],[0,0,1]])):

    origin_a = np.array(origin).astype(np.float32)
    voxel_size_a = np.array(voxel_size).astype(np.float32)
    coord_a = np.array(coord_xyz).astype(np.float32)

    print('origin_a', origin_a)
    print('voxel_size_a', voxel_size_a)
    print('coord_a', coord_a)

    cri_a = ((coord_a - origin_a) @ np.linalg.inv(orientation)) / voxel_size_a
    
    print('cri_a', cri_a)

    # it can only be whole numbers as irc
    cri_a = np.round(cri_a)
    return IrcTuple(index=int(cri_a[2]), row=int(cri_a[1]), col=int(cri_a[0]))

def irc2xyz(coord_irc, origin_xyz, vxSize_xyz, direction_a):
    cri_a = np.array(coord_irc)[::-1]
    origin_a = np.array(origin_xyz)
    vxSize_a = np.array(vxSize_xyz)
    coords_xyz = (direction_a @ (cri_a * vxSize_a)) + origin_a
    # coords_xyz = (direction_a @ (idx * vxSize_a)) + origin_a
    return XyzTuple(*coords_xyz)


In [32]:
combined = pd.merge(exclusions, metadata, left_on='seriesuid', right_on='scan_id', how='outer')  

for col in ['coordX', 'coordY', 'coordZ', 'diameter_mm',
       'x-offset', 'y-offset', 'z-offset', 'x-spacing', 'y-spacing',
       'z-spacing', 'x-pixels', 'y-pixels', 'slices']:
    combined[col] = combined[col].astype(float)

combined

seriesuid      coordX  \
0      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222... -131.896494   
1      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222...   80.798736   
2      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222...  -62.287146   
3      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222...   83.376859   
4      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222...  -41.017623   
...                                                  ...         ...   
35187  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084...  -45.043687   
35188  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084...  -31.567113   
35189  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084...  -38.598369   
35190  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084...   29.370439   
35191  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084...   52.807959   

           coordY  coordZ  diameter_mm  \
0     -155.056702 -317.80         -1.0   
1     -109.295001 -123.40         -1.0   
2      -55.154396 -283.60         -1.0   
3      -58.377052 -236.80         -1.0   
4      -60.310645 -240.40         -1.0   
...           ...     ...          ...   
35187   57.018889  -99.11         -1.0   
35188   20.690733  -15.36         -1.0   
35189   39.440749 -179.11         -1.0   
35190   16.589167   15.89         -1.0   
35191   51.159509    5.89         -1.0   

                                                 scan_id    x-offset  \
0      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222... -157.677730   
1      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222... -157.677730   
2      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222... -157.677730   
3      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222... -157.677730   
4      1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222... -157.677730   
...                                                  ...         ...   
35187  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084... -155.199997   
35188  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084... -155.199997   
35189  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084... -155.199997   
35190  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084... -155.199997   
35191  1.3.6.1.4.1.14519.5.2.1.6279.6001.997611074084... -155.199997   

         y-offset    z-offset  x-spacing  y-spacing  z-spacing  x-pixels  \
0     -311.677730 -438.400000   0.644531   0.644531       1.80     512.0   
1     -311.677730 -438.400000   0.644531   0.644531       1.80     512.0   
2     -311.677730 -438.400000   0.644531   0.644531       1.80     512.0   
3     -311.677730 -438.400000   0.644531   0.644531       1.80     512.0   
4     -311.677730 -438.400000   0.644531   0.644531       1.80     512.0   
...           ...         ...        ...        ...        ...       ...   
35187 -142.199997 -316.609985   0.585938   0.585938       1.25     512.0   
35188 -142.199997 -316.609985   0.585938   0.585938       1.25     512.0   
35189 -142.199997 -316.609985   0.585938   0.585938       1.25     512.0   
35190 -142.199997 -316.609985   0.585938   0.585938       1.25     512.0   
35191 -142.199997 -316.609985   0.585938   0.585938       1.25     512.0   

       y-pixels  slices  
0         512.0   194.0  
1         512.0   194.0  
2         512.0   194.0  
3         512.0   194.0  
4         512.0   194.0  
...         ...     ...  
35187     512.0   285.0  
35188     512.0   285.0  
35189     512.0   285.0  
35190     512.0   285.0  
35191     512.0   285.0  

[35192 rows x 15 columns]

In [33]:



exclusions_output = {}

for idx, row in combined.iterrows():

    coord_xyz = XyzTuple(row.coordX, row.coordY, row.coordZ)
    irc = xyz2irc(coord_xyz, row[['x-offset', 'y-offset', 'z-offset']], row[['x-spacing', 'y-spacing', 'z-spacing']])

    exclusions_output[row.seriesuid] = {
        'coordX' : irc.col,
        'coordY' : irc.row,
        'coordZ' : irc.index,
        'diameter_mm' : row.diameter_mm,
    }



origin_a [-157.67773 -311.67773 -438.4    ]
voxel_size_a [0.64453125 0.64453125 1.8       ]
coord_a [-131.8965 -155.0567 -317.8   ]
cri_a [ 39.99997633 242.9999053   67.00000517]
origin_a [-157.67773 -311.67773 -438.4    ]
voxel_size_a [0.64453125 0.64453125 1.8       ]
coord_a [  80.79874 -109.295   -123.4    ]
cri_a [369.99985795 313.99988163 175.00000464]
origin_a [-157.67773 -311.67773 -438.4    ]
voxel_size_a [0.64453125 0.64453125 1.8       ]
coord_a [ -62.287148  -55.154396 -283.6     ]
cri_a [147.99994081 397.99985795  85.9999955 ]
origin_a [-157.67773 -311.67773 -438.4    ]
voxel_size_a [0.64453125 0.64453125 1.8       ]
coord_a [  83.37686   -58.377052 -236.8     ]
cri_a [373.99985795 392.99985795 111.99999788]
origin_a [-157.67773 -311.67773 -438.4    ]
voxel_size_a [0.64453125 0.64453125 1.8       ]
coord_a [ -41.017624  -60.310646 -240.4     ]
cri_a [180.99992898 389.99985795 110.00000291]
origin_a [-157.67773 -311.67773 -438.4    ]
voxel_size_a [0.64453125 0.64453125 1.8 

In [35]:
pd.DataFrame.from_dict(exclusions_output, orient='index').reset_index().to_csv('pixel_exclusions.csv', index=False)